The goal of this notebook is to build a simple, end-to-end prototype for how we will be modeling the V1-MT motion perception pipeline:
- Generate a drifting sinusodial stimulus
- Compute local motion energy signals with a bank of Gabor Filters to simulate V1 complex cell outputs
- Generate a synthentic spike train from a Poisson process (this will be replaced with real MT data in the actual model)
- Fit a Poisson GLM, using the motion energy features, to the single, synthetic MT neuron
- Show that we can recover the synthetic spike train


Actual experimental conditions from the paper where the MT recordings are from:

> Monkeys sat in a primate chair (Crist Instruments) and faced a 55 inch LCD (LG) display (resolution = 1920 × 1080p, refresh rate = 60Hz, background luminance − 26.49 cd/m2) that was corrected to have a linear gamma function. Monkeys viewed the stimulus from a distance of 118cm such that the screen subtended 100 degrees of visual angle.

In [3]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import fftconvolve
from numpy.typing import NDArray
from matplotlib.animation import FuncAnimation
%matplotlib inline


# Drifting sinusoidal grating

## 2D Sinusoidals

In [5]:
def sinusoidal_2d(
    x: NDArray[np.floating],
    y: NDArray[np.floating],
    theta: float,
    A: float,
    f: float,
    phase: float,
) -> NDArray[np.floating]:
    # TODO: What is a typical domain used in real world stimuli?
    # TODO: What is an intuitive way to understand when frequency, time buckets and time constants
    #       in this context? 
    X, Y = np.meshgrid(x, y)
    X_rot = X * np.cos(theta) + Y * np.sin(theta) 
    return A * np.cos((2 * np.pi * f * X_rot) + phase)

def render_sinusodial_2d(sinusodial: NDArray[np.floating], title: str):
    plt.figure()
    plt.imshow(sinusodial, cmap='gray', origin='lower')
    plt.colorbar()
    plt.title(title)
    plt.xlabel('X')
    plt.ylabel('Intensity')
    plt.show()

def test_sinusoidal_2d():
    L = 1 
    x, y = np.linspace(0, L, 100), np.linspace(0, L, 100)
    theta = np.pi / 4
    A = 1.0
    f = 4
    phase = 0.0
    sinusodial = sinusoidal_2d(x, y, theta, A, f, phase)
    render_sinusodial_2d(sinusodial, f'A basic 2D sinusodial oriented at {theta}')

Define a function to calculate the pixel pitch (deg / px) given a viweing distance, monitor resolution and monitor length. This allows us to accurately map the psychophysical definition of a stimulus or filter (i.e in visual degrees) to the quantized, pixel lattice we construct. 

## 3D drifting grating stimulus

In [ ]:
from motionenergy import drifting_sinusoidal, utils
from IPython.display import HTML, display

def create_and_render_stimulus():
    speed = 5.0 # degrees/s
    size = (20.0, 20.0) # degrees
    theta = 45 # degrees
    spatial_frequency = 0.3 # cycle/deg
    amplitude = 1.0
    time = 5.0 # seconds
    fps = 60 # Hz
    monitor_resolution = (500, 500)
    viewing_distance = 100 # cm
    monitor_length = 20 # in

    # Calculate the degrees / px and the px / inch (dpi)
    (px_pitch, dpi) = utils.pixel_pitch(
        viewing_distance,
        monitor_resolution,
        monitor_length,
    )

    print(f"Calculated pixel pitch: {px_pitch} and dpi: {dpi}")
    stimulus = drifting_sinusoidal.new_stimulus(
        speed,
        size,
        theta,
        0, # phase
        spatial_frequency,
        amplitude,
        time,
        fps,
        px_pitch
    )

    width, height = stimulus.shape[1], stimulus.shape[2]
    print(f"Returned stimulus of size: {stimulus.shape}")

    return drifting_sinusoidal.animate_stimulus(
        stimulus,
        int(np.ceil(fps*time)), # number of frames
        fps,
        width,
        height,
        dpi,
        'Drifting Sinusoidal'
    )

ani = create_and_render_stimulus()
display(HTML(ani.to_jshtml()))


Calculated pixel pitch: 0.041162460204278085 and dpi: 35
Calculated width and height of stimulus in pixels as: 486, 486
Returned stimulus of size: (300, 486, 486)


# Compute local motion energy with a bank of filters

In [51]:
from motionenergy import gabor, utils

def test_single_spatial_filter():
    theta = np.pi / 4
    f_s = 0.3      # cyc/deg  → σ = 0.5
    k = gabor.new_spatial_filter(theta, 0, f_s, 0.02)
    print(k.shape)  # expect ≈ (151, 151)  because 6σ / 0.02 ≈ 150 px

    g = gabor.new_spatial_filter(theta_deg=45,
                                phase=0,
                                f_s=4,
                                pixel_pitch=0.03)   # ≈ 34 px per deg

    print(g.shape)                  # (k, k) with k odd (e.g. 29×29)
    print(g.mean())                 # ≈ 0
    print(np.sqrt((g**2).sum()))    # 1.0

def test_spatial_gabor_filter():
    monitor_resolution = (500, 500)
    viewing_distance = 100 # cm
    monitor_length = 20 # in
    px_pitch, dpi = utils.pixel_pitch(viewing_distance, monitor_resolution, monitor_length)     # deg/px
    thetas = [0, 45, 90, 135, 180]
    frequencies = [0.25, 0.5, 1] # cycles/deg
    phases = [0, np.pi]

    gabors = []
    for theta in thetas:
        for f in frequencies:
            for phase in phases:
                filter = gabor.new_spatial_filter(theta, phase, f, px_pitch) 
                gabors.append(filter)

    # gabors = np.array(gabors)
    print(len(gabors))
    gabor.plot_spatial_gabors(gabors, dpi, 'Spatial Gabors')

# test_single_spatial_filter()
test_spatial_gabor_filter()



30
--> plotting 30 kernels
--> plotting 6 rows with 5 plots per row


In [53]:
from motionenergy import gabor, utils, motion_energy

monitor_resolution = (500, 500)
viewing_distance = 100 # cm
monitor_length = 20 # in
px_pitch, dpi = utils.pixel_pitch(viewing_distance, monitor_resolution, monitor_length)     # deg/px

def test_motion_energy():
    L = 1 
    x, y = np.linspace(0, L, 200), np.linspace(0, L, 200)
    theta = np.pi / 4
    A = 1.0
    f = 2
    phase = 0.0
    frames = 50
    temporal_f = 3

    thetas_deg = np.arange(0, 180, 22.5) # 0 to 180 every 22.5deg
    frequencies = [1.0, 2.0, 4.0] # cycles/deg
    filters, channels = gabor.new_filter_bank(frequencies, thetas_deg, px_pitch)
    print(f"number of even filters: {len(filters[0])}, number of odd filters: {len(filters[1])}")

    stimulus = drifting_sinusoidal.sinusoidal_3d(x, y, theta, A, f, temporal_f, frames)
    energy = motion_energy.compute_features(stimulus, filters, channels)
    print(energy)
    

    
    

Calculated width and height of stimulus in pixels as: 250, 250
Calculated width and height of stimulus in pixels as: 250, 250


--> plotting 24 kernels
--> plotting 5 rows with 5 plots per row


AssertionError: root mean squared error was: 24.66561092858409

# Generate synthetic spikes from a Poisson process with hard-coded weights 


# Fit a Poisson GLM to the synthetic spikes to recover the real weights 

In [8]:
x = np.arange(0, 2, 1)
y = np.arange(4, 8, 1)
t = np.arange(9, 20, 1)

T, X, Y = np.meshgrid(t, x, y, indexing = 'ij')

print(f'T: {T}, {T.shape}')
print(f'X: {X}, {X.shape}')
print(f'Y: {Y}, {Y.shape}')

T: [[[ 9  9  9  9]
  [ 9  9  9  9]]

 [[10 10 10 10]
  [10 10 10 10]]

 [[11 11 11 11]
  [11 11 11 11]]

 [[12 12 12 12]
  [12 12 12 12]]

 [[13 13 13 13]
  [13 13 13 13]]

 [[14 14 14 14]
  [14 14 14 14]]

 [[15 15 15 15]
  [15 15 15 15]]

 [[16 16 16 16]
  [16 16 16 16]]

 [[17 17 17 17]
  [17 17 17 17]]

 [[18 18 18 18]
  [18 18 18 18]]

 [[19 19 19 19]
  [19 19 19 19]]], (11, 2, 4)
X: [[[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]

 [[0 0 0 0]
  [1 1 1 1]]], (11, 2, 4)
Y: [[[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]

 [[4 5 6 7]
  [4 5 6 7]]], (11, 2, 4)
